In [1]:
import json
from src.surquest.utils.appstoreconnect.credentials import Credentials
from src.surquest.utils.appstoreconnect.analyticsreports.client import Client
from src.surquest.utils.appstoreconnect.analyticsreports.handler import Handler
from src.surquest.utils.appstoreconnect.analyticsreports.enums.category import Category
from src.surquest.utils.appstoreconnect.analyticsreports.enums.granularity import Granularity
from src.surquest.utils.appstoreconnect.analyticsreports.enums.report_name import ReportName
from pathlib import Path

In [2]:
key_path = Path.cwd() / "credentials" / "key.p8"
CATEGORY = Category.FRAMEWORK_USAGE
REPORT_NAME = ReportName.APP_STORE_INSTALLATION_AND_DELETION_STANDARD
GRANULARITY = Granularity.DAILY
# DATE = "2025-07-27"
APP_ID = "950949627"

KEY_ID = '5WDUV3USAU' # 10-character key ID from App Store Connect
ISSUER_ID = '69a6de80-fd44-47e3-e053-5b8c7c11a4d1'  # 36-character issuer ID
PRIVATE_KEY = key_path.read_text()
CSV_PATH = Path.cwd() / "data" / APP_ID / f"{REPORT_NAME.name}.data.csv"
JSON_PATH = Path.cwd() / "data" / APP_ID / f"{REPORT_NAME.name}.data.json"

credentials = Credentials(
    issuer_id=ISSUER_ID, # 36-character issuer ID
    key_id=KEY_ID, # 10-character key ID from App Store Connect
    private_key=PRIVATE_KEY
)
client = Client(credentials=credentials)

data = client.get_data(
    app_id = APP_ID,
    report_name = REPORT_NAME
)

Handler.list_of_dicts_to_csv(data, CSV_PATH)
Handler.list_of_dicts_to_jsonl(data, JSON_PATH)



print(json.dumps(Handler.extract_attribute_values(data), indent=4))



INFO     - 2025-08-03 17:00:53,372 - Initialized Client with provided credentials
Bad pipe message: %s [b' 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/138.0.0.0 Sa']
Bad pipe message: %s [b'ri/537.36\r\nAccept: text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/', b'ng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.7\r\nAccept-Encoding: gzip, deflate, br, zstd\r\nA']
Bad pipe message: %s [b'ept-Language: en-GB,en-US;q=0.9,en;q=0.8,de;q=0.7,ru;q=0.6\r\nPriority: u=0, i\r\nReferer: https://stu', b'o.firebase.google.com/\r\nSec-Ch-Ua: "Not)A;Brand";v="8", "Chromium";v="138", "Google Chrome";v="138"', b'Sec-Ch-Ua-Ar']
Bad pipe message: %s [b': "x86"\r\nSec-Ch-Ua-Bitness: "64"\r\nSec-Ch-Ua-Form-Factors: "Desktop"\r\nSec-Ch-Ua-Full-Version: "138.']
Bad pipe message: %s [b'7204.184"\r\nSec-Ch-Ua-Full-Version-List: "Not)A;']
Bad pipe message: %s [b'and";v="8.0.0.0", "Chromium";v="138.0.7204.184", "Google Chrome";']
Bad pipe message: %s [b'"138

NoValidUrlsError: No valid `None` found in the payload.

In [ ]:
from enum import Enum

class App(str, Enum):

    LRT = "950949627"
    LGO = "1207764294"
    MV = "6451202232"

for app in [App.LRT, App.LGO, App.MV]:

    report_requests = client.read_report_requests(
        app_id=app.value
    )

    print(f"{app.name}: report requests {len(report_requests)} - {report_requests}")


    if len(report_requests) == 0:

        client.create_report_request(app_id = app.value)

In [ ]:
app = "6451202232"
report_requests = client.read_report_requests(
    app_id=app
)

report_requests
print(report_requests)
report_requests_id = report_requests[0].get("id")

specific_request = client.read_report_for_specific_request(
    report_requests_id,
    params={
        "filter[category]": REPORT_NAME.category.value,
        "filter[name]":REPORT_NAME.value
    }
)
print(specific_request)
specific_request_id = specific_request[0].get("id")
specific_request_ids = Handler.extract_ids(specific_request)

for i in specific_request_ids:

    instances = client.read_list_of_instances_of_report(specific_request_id)
    print(i, len(instances))
    print(instances)
    print()

In [ ]:
#1A Read Report Requests
report_requests = client.read_report_requests(app_id=APP_ID)
report_request_id = report_requests.get("data")[0].get("id")
RenderJSON(report_requests)


In [ ]:
#2A Read Report
report = client.read_report_for_specific_request(
    request_id=report_request_id,
    params={
        "filter[category]": CATEGORY.value,
        "filter[name]": REPORT_NAME
    }
)

report_id = report.get("data")[0].get("id")
print(report_id)
print(report)
RenderJSON(report)

In [ ]:
#3A Read Report Instances
instances = client.read_list_of_instances_of_report(
    report_id=report_id,
    params={
        "filter[granularity]": GRANULARITY.value,
        "filter[processingDate]": DATE
    }
)
instance_id = instances.get("data")[0].get("id")
RenderJSON(instances)

In [ ]:
#4 Get segments
segments = client.read_segments_for_report(
    instance_id=instance_id
)
url  = segments.get("data")[0].get("attributes").get("url")
RenderJSON(segments)


In [ ]:
# Download the report data
data = client.download_report_to_dicts(
    report_url=url
)
data

In [ ]:
client.get_data(
    app_id = APP_ID,
    report_name = REPORT_NAME,
    category = CATEGORY,
    granularity = GRANULARITY,
    dates = {'2025-07-25', '2025-07-26'}
)
